In [1]:
import numpy as np
import matplotlib.pyplot as plt
import wget
import pandas as pd
from seebuoy import NDBC
import requests

In [315]:
trunk_locations = [[25,35], [100,130], [220, 240]]
lengths1 = [400, 1000, 900]
lengths2 = [600, 600, 400]
nParticles = 10000
maxX = 300
maxY = 350

In [391]:
#note, this function expects a matrix A[ix,iy] 
#and then displays so that A[:,0] is the lowest row of pixels
def display(A):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.ones((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    %matplotlib qt 
    
    plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    plt.imshow(B, cmap = 'terrain'); 
    plt.axis('off'); 
    plt.show()
    plt.draw()
    plt.pause(0.01)

In [390]:
def get_weather_data():
    api_key = '037d526b36fc10eddbdb6d6570692689'
    lat = 37.773972
    long = -122.431297
    url = f'https://api.openweathermap.org/data/3.0/onecall?lat={lat}&lon={long}&appid={api_key}'
    response = requests.get(url).json()
    current_info = response['current']
    wind_deg = current_info['wind_deg']
    wind_speed = current_info['wind_speed']
    current_weather = current_info['weather']
    weather_desc = current_weather[0]['main']
    sun_x = (current_info['dt'] - current_info['sunrise'])/abs(current_info['sunrise']- current_info['sunset'])
    #return response
    return wind_deg, wind_speed, weather_desc, sun_x

#ensure sun_x will display sun or moon in appropraite part of sky.  ishould just need to use the fraction and take that out of maxX and then if it is negative or > maxX then present the moon somewhere random....

date = 11-25-2023
tz = '-08:00'
#print(get_weather_data())

def generate_clouds(Mat):
    x = np.linspace(0, maxX)
    y = np.sin(x) + 10
    for i in range(maxX):
        for j in range(maxY):
            if j > (25*np.sin(2*i) + 300):
                Mat[i, j] = .88
    display(Mat)




def direction_of_branches(direction):
    if direction < 180:
        favor_right = True
    else:
        favor_right = False
    return favor_right


def generate_sun(Mat, x_location):
    for x in range(maxX):
        for y in range(maxY):
            if (x-x_location)**2 + (y-310)**2 < 20**2:
                Mat[x, y] = .4
    display(Mat)

def generate_moon(Mat, x_location):
    for x in range(maxX):
        for y in range(maxY):
            if (x-30)**2 + (y-270)**2 < 20**2:
                Mat[x, y] = .95


    display(Mat)

In [680]:

#Creates a basemap with location of trunks
def create_base_map(trunk_locations):

# Initialize matrix containing all 2D grid points A(x,y)
    A = np.zeros((maxX, maxY))
    for i in range(maxX):
        for j in range(maxY):
            if j < 45:
                A[:, j] = .7

# Introduce a sticky wall at the bottom 
# by filling parts of the lowest row of pixels with particles
    for trunk_base in trunk_locations:
        A[trunk_base[0]: trunk_base[1], 0] = .8
    #print(A.transpose())
    return A






#Builds several different trees at predefined thickness and predefined length based on thickness.
def build_trunks(A, trunk_locations, lengths):
    for item, base in enumerate(trunk_locations):
        yBuffer = 5
        yStart  = 1 + yBuffer
        length = lengths[item]
        for i in range(0,length):
        # Compute new starting point on the line y=yStart
            x  = np.random.randint(base[0], base[1])
            y  = yStart; #always start at upper limit

            while True:
                xOrg = x
                yOrg = y

                r = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle
            #left, right, up, or down and change x and y accordingly
                if r <.05:
                    x = (x + 1) % maxX
            #elif direction_val == 1:
                elif r <.1:
                    x = (x - 1) % maxX
            #elif direction_val == 2:
                elif r < .14:
                    y = (y + 1) % maxY
                else:
                    y = (y - 1) % maxY
            
            #now apply periodic boundary conditions to 'x'
    
            
                if (A[x,y] == .8 or y>yStart): 
                    x = xOrg
                    y = yOrg
                    continue; # if this site has been taken try moving in a different direction
            
            #determine the x coordionates of the left and right neighbors
            #store them in 'xm' and 'xp' and apply periodic boundary conditions again
                xp = (x + 1) % maxX
                xm = (x - 1) % maxX
                yp = y+1
                ym = y-1
    
            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
                if (A[xp, y] == .8 or A[x, ym] == .8 or A[xm, y] == .8 or A[x, yp] == .8): 
                    A[x,y] = .8
                    if (y+yBuffer>yStart and y+yBuffer<maxY): 
                        yStart = y+yBuffer

                    # if (i%1000==0): 
                    #     print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')

                    nNewParticlesPerFrame = 200 
                    if (i%nNewParticlesPerFrame==0): 
                        display(A)
                    
                    break # particle was attached, break out of current loop and insert next one
                
            if (yStart+1==maxY): 
                print(f'Structures reached Y limit after only {i} particles')
                break
    display(A)






#Identify about where tops of the trunks are located and then draws a line so the branches can grow from
def tops_trunks(trunk_locations, A):
    tops_trunks = []
    for base in trunk_locations:
        top_trunk = 0
        for i in range(A.shape[1]//2):
            if sum(A[base[0]:base[1],i] == .8) > 2:
                top_trunk = i
        tops_trunks.append(top_trunk)
    return tops_trunks






#Builds branches, I will make them green. These branches should sway right
def build_branches_left(A, trunk_locations, direction, lengths, tops_trunks, inverse = False):
    if inverse:
        trunk_locations = [trunk_locations[2], trunk_locations[1], trunk_locations[0]]
        tops_trunks = [tops_trunks[2], tops_trunks[1], tops_trunks[0]]
    for item, base in enumerate(trunk_locations):
        yBuffer = 1
        yStart = tops_trunks[item] + yBuffer
        x_min = base[0]

        for i in range(6000):
        # Compute new starting point on the line y=yStart
            x  = np.random.choice(np.arange(base[0], base[1]))
            y  = yStart; #always start at upper limit

            while True:
                xOrgr = x
                yOrgr = y
                #print(x, y)

                r = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle
            #the wind direction motivates the direction of branches. Either easterly movement(right) or westerly(left). 
                if r <.35:
                    if (x + 1) < (maxX - 1):
                        x = (x + 1)
                    else:
                        x = x-1
            #elif direction_val == 1:
                elif r <.45:
                    if (x - 1) > 0:
                        x = (x - 1)
                    else:
                        x = x+1
            #elif direction_val == 2:
                elif r < .6:
                    y = (y + 1) %maxY
                else:
                    y = (y - 1) 

            
                #if (A[x,y] == 1 or y>yStart): 
                if (A[x,y] == .35): 
                    x = xOrgr
                    y = yOrgr
                    continue; # if this site has been taken try moving in a different direction
            
            #determine the x coordionates of the left and right neighbors
            #store them in 'xm' and 'xp' and apply periodic boundary conditions again
                if (x + 1) > maxX-1:
                    xp = x - 1
                else:
                    xp = x+2

                if (x - 1) < 0:
                    xm = x + 2
                else:
                    xm = x-1
                    
                yp = (y+1)
                ym = (y-2) 
                if x < 20:
                    break


            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
                #print(sum(np.array(A[xm:xp, ym:yp]).flatten() == .35))
                if (sum(np.array(A[xm:xp, ym:yp]).flatten() == .35)> 1):
                    # if x < x_min-30:
                    #     break
                    A[x,y] = .35
                    if (y+yBuffer > yStart and y+yBuffer < maxY - 1): 
                        yStart = y + yBuffer

                    # if (i%1000==0): 
                    #     print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')

                    nNewParticlesPerFrame = 200 
                    if (i%nNewParticlesPerFrame==0): 
                        display(A)
                    
                    break # particle was attached, break out of current loop and insert next one
                
            if (yStart+1>=maxY-120): 
                print(f'Structures reached Y limit after only {i} particles')
                break
    display(A)



    #Builds branches, I will make them green. These should sway left.
def build_branches_right(A, trunk_locations, direction, lengths, tops_trunks, inverse = False):
    if inverse:
        trunk_locations = [trunk_locations[2], trunk_locations[1], trunk_locations[0]]
        tops_trunks = [tops_trunks[2], tops_trunks[1], tops_trunks[0]]
    for item, base in enumerate(trunk_locations):
        yBuffer = 1
        yStart = tops_trunks[item] + yBuffer
        x_min = base[0]

        for i in range(6000):
        # Compute new starting point on the line y=yStart
            x  = np.random.choice(np.arange(base[0], base[1]))
            y  = yStart; #always start at upper limit

            while True:
                xOrgr = x
                yOrgr = y
                #print(x, y)

                r = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle
            #the wind direction motivates the direction of branches. Either easterly movement(right) or westerly(left). 
                if r <.1:
                    if (x + 1) < (maxX - 1):
                        x = (x + 1)
                    else:
                        x = x-1
            #elif direction_val == 1:
                elif r <.45:
                    if (x - 1) > 0:
                        x = (x - 1)
                    else:
                        x = x+1
            #elif direction_val == 2:
                elif r < .6:
                    y = (y + 1) %maxY
                else:
                    y = (y - 1) 

            
                #if (A[x,y] == 1 or y>yStart): 
                if (A[x,y] == .35): 
                    x = xOrgr
                    y = yOrgr
                    continue; # if this site has been taken try moving in a different direction
            
            #determine the x coordionates of the left and right neighbors
            #store them in 'xm' and 'xp' and apply periodic boundary conditions again
                if (x + 1) > maxX-1:
                    xp = x - 1
                else:
                    xp = x+2

                if (x - 1) < 0:
                    xm = x + 2
                else:
                    xm = x-1
                    
                yp = (y+1)
                ym = (y-2) 
                if x < 20:
                    break


            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
                #print(sum(np.array(A[xm:xp, ym:yp]).flatten() == .35))
                if (sum(np.array(A[xm:xp, ym:yp]).flatten() == .35)> 1):
                    # if x < x_min-30:
                    #     break
                    A[x,y] = .35
                    if (y+yBuffer > yStart and y+yBuffer < maxY - 1): 
                        yStart = y + yBuffer

                    # if (i%1000==0): 
                    #     print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')

                    nNewParticlesPerFrame = 200 
                    if (i%nNewParticlesPerFrame==0): 
                        display(A)
                    
                    break # particle was attached, break out of current loop and insert next one
                
            if (yStart+1>=maxY-120): 
                print(f'Structures reached Y limit after only {i} particles')
                break
    display(A)




In [639]:
def generate_scene(trunk_locations, lengths1, lengths2):
    A = create_base_map(trunk_locations)
    print('The trunks are at:', trunk_locations)
    print('Basemap Created')
    weather = get_weather_data()
    print(f'Weather has been identified: Windspeed:{weather[1]} mph, Wind Direction:{weather[0]}, Weather descripter:{weather[2]}')
    #weather = (60.5, 2.2, 'Clouds', .8)
    if weather[3]>0 and weather[3]<1:
        generate_sun(A, weather[3]*maxX)
    else:
        generate_moon(A, (weather[3]%1)*maxX)
    if weather[2] == 'Clouds':
        generate_clouds(A)
    build_trunks(A, trunk_locations, lengths = lengths1)
    tops_trunks_vlas = tops_trunks(trunk_locations, A)
    print('Trunks have been grown')

    for i, top in enumerate(tops_trunks_vlas):
        for j in range(trunk_locations[i][0], trunk_locations[i][1]):
            A[j, top-1: top+1] = .35
    display(A)
    print('The tops of trunks are at:',   tops_trunks_vlas)
    if direction_of_branches(weather[0]):
        print('Wind favors right')
        build_branches_right(A, trunk_locations, direction = 0, lengths = lengths2, tops_trunks=tops_trunks_vlas)
    else:
        print('wind favors left')
        build_branches_left(A, trunk_locations, direction = 0, lengths = lengths2, tops_trunks=tops_trunks_vlas)

    

In [681]:

generate_scene(trunk_locations, lengths1, lengths2)


The trunks are at: [[25, 35], [100, 130], [220, 240]]
Basemap Created
Weather has been identified: Windspeed:1.79 mph, Wind Direction:94, Weather descripter:Clouds
Trunks have been grown
The tops of trunks are at: [83, 70, 97]
Wind favors right
Structures reached Y limit after only 426 particles
Structures reached Y limit after only 1290 particles
Structures reached Y limit after only 2420 particles
